In [31]:
%pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cpu


Looking in indexes: https://download.pytorch.org/whl/cpu
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 26.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [32]:
%pip install stable-baselines3[extra] protobuf==3.20.*

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 26.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [33]:
%pip install mss pydirectinput pytesseract

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.2 -> 26.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [34]:
#chrome://dino/

In [35]:
import pytesseract
pytesseract.pytesseract.tesseract_cmd = r"C:\Program Files\Tesseract-OCR\tesseract.exe"


In [36]:
from mss import mss
import pydirectinput
import cv2
import numpy as np
import pytesseract
from matplotlib import pyplot as plt
import time
import gymnasium as gym
from gymnasium import spaces

In [37]:
import numpy as np
import cv2
import time
import gymnasium as gym
from gymnasium import spaces
from mss import mss
import pydirectinput

pydirectinput.PAUSE = 0  # IMPORTANT for FPS


class WebGame(gym.Env):
    metadata = {"render_modes": []}

    def __init__(self):
        super().__init__()
        self.steps_since_reset = 0
        self.steps_alive = 0



        # Observation: grayscale frame
        self.observation_space = spaces.Box(
            low=0, high=255, shape=(1, 48, 48), dtype=np.uint8
        )

        # Actions:
        # 0 = jump
        # 1 = duck
        # 2 = do nothing
        self.action_space = spaces.Discrete(3)

        self.cap = mss()

        # Track key state
        self.last_action = None
        self.ducking = False

        # Gameplay ROI (Dino + obstacles)
        self.game_location = {
            "top": 300,
            "left": 0,
            "width": 400,
            "height": 120
        }

        # GAME OVER text ROI (LOCKED)
        self.done_location = {
            "top": 190,
            "left": 820,
            "width": 300,
            "height": 60
        }
    
    def reset(self, seed=None, options=None):
        self.steps_alive = 0

        self.steps_since_reset = 0

        super().reset(seed=seed)

        # Release any stuck keys
        pydirectinput.keyUp("down")
        self.ducking = False
        self.last_action = None

        # Restart game
        pydirectinput.click(x=150, y=150)
        pydirectinput.press("space")

        return self.get_observation(), {}

    def step(self, action):
        # ----- ACTION HANDLING -----
        self.steps_alive += 1

        if action == 0:  # JUMP
            if self.last_action != 0:
                pydirectinput.keyUp("down")
                pydirectinput.press("space")
                self.ducking = False

        elif action == 1:  # DUCK
            if not self.ducking:
                pydirectinput.keyDown("down")
                self.ducking = True

        elif action == 2:  # NO OP
            if self.ducking:
                pydirectinput.keyUp("down")
                self.ducking = False

        self.last_action = action

        # ----- ENV STEP -----
        observation = self.get_observation()
        self.steps_since_reset += 1

        if self.steps_since_reset < 6:
            terminated = False
        else:
                terminated = self.get_done()

        truncated = False

        reward = 1.0

        if terminated:
            reward = -15.0
        

        return observation, reward, terminated, truncated, {}

    def get_observation(self):
        frame = np.array(self.cap.grab(self.game_location))[:, :, :3]
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        resized = cv2.resize(gray, (48, 48))
        return resized.reshape(1, 48, 48)

    def get_done(self):
        frame = np.array(self.cap.grab(self.done_location))[:, :, :3]
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

        edges = cv2.Canny(gray, 50, 150)
        edge_density = (edges > 0).mean()

        return edge_density > 0.014

    def close(self):
        pydirectinput.keyUp("down")
        cv2.destroyAllWindows()


In [38]:
env = WebGame()
obs, info = env.reset()

import time

# Warm-up (important for stable FPS)
for _ in range(20):
    env.step(2)  # NO-OP

start = time.time()

for _ in range(200):
    # Sample random action (0=jump, 1=duck, 2=no-op)
    obs, reward, terminated, truncated, info = env.step(
        env.action_space.sample()
    )

    if terminated:
        obs, info = env.reset()

end = time.time()

fps = 200 / (end - start)
print("FPS:", fps)

env.close()


FPS: 33.231279078975575


In [39]:
import numpy as np
from stable_baselines3.common.callbacks import BaseCallback

class EarlyStopCallback(BaseCallback):
    def __init__(self, eval_env, score_threshold=350, eval_episodes=3, verbose=1):
        super().__init__(verbose)
        self.eval_env = eval_env
        self.score_threshold = score_threshold
        self.eval_episodes = eval_episodes

    def _on_step(self) -> bool:
        # Evaluate every 5000 steps
        if self.n_calls % 5000 != 0:
            return True

        scores = []

        for _ in range(self.eval_episodes):
            obs, _ = self.eval_env.reset()
            done = False
            total_reward = 0

            while not done:
                action, _ = self.model.predict(obs, deterministic=True)
                obs, reward, terminated, truncated, _ = self.eval_env.step(int(action))
                done = terminated or truncated
                total_reward += reward

            scores.append(total_reward)

        mean_score = np.mean(scores)

        print(f"[EarlyStop] Mean Eval Score: {mean_score:.2f}")

        if mean_score >= self.score_threshold:
            print(f"\n🎯 TARGET REACHED: {mean_score:.2f} ≥ {self.score_threshold}")
            print("🛑 Early stopping training...\n")

            self.model.save("dqn_dino_350plus")
            return False   # THIS stops training

        return True


In [40]:
import os
from stable_baselines3 import DQN
from stable_baselines3.common.callbacks import EvalCallback, BaseCallback
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import DummyVecEnv, VecFrameStack


# ---------- ENV ----------
def make_env():
    return Monitor(WebGame())


train_env = DummyVecEnv([make_env])
eval_env = DummyVecEnv([make_env])

train_env = VecFrameStack(train_env, n_stack=4)
eval_env = VecFrameStack(eval_env, n_stack=4)


# ---------- PATHS ----------
CHECKPOINT_DIR = "./train/"
LOG_DIR = "./logs/"
BEST_MODEL_DIR = "./best_model/"
EVAL_LOG_DIR = "./eval_logs/"


# ---------- CHECKPOINT CALLBACK ----------
class TrainAndLoggingCallback(BaseCallback):
    def __init__(self, check_freq, save_path, verbose=0):
        super().__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path

    def _init_callback(self):
        os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            self.model.save(os.path.join(self.save_path, f"model_{self.n_calls}"))
        return True


checkpoint_callback = TrainAndLoggingCallback(
    check_freq=10_000,
    save_path=CHECKPOINT_DIR
)


# ---------- EVAL CALLBACK ----------
eval_callback = EvalCallback(
    eval_env,
    best_model_save_path=BEST_MODEL_DIR,
    log_path=EVAL_LOG_DIR,
    eval_freq=5_000,
    deterministic=True,
    render=False,
    verbose=1
)


# ---------- DOUBLE + DUELING DQN ----------
model = DQN(
    policy="CnnPolicy",
    env=train_env,
    learning_rate=7e-5,
    buffer_size=60_000,
    learning_starts=5_000,
    batch_size=32,
    gamma=0.99,
    exploration_fraction=0.7,
    exploration_final_eps=0.08,
    target_update_interval=1_000,
    train_freq=4,
    gradient_steps=1,
    tensorboard_log=LOG_DIR,
    verbose=1,
    device="cpu"
)



# ---------- TRAIN ----------
model.learn(
    total_timesteps=150_000,
    callback=[checkpoint_callback, eval_callback],
    log_interval=1
)


Using cpu device


c:\Users\rudra\RL_Project\rl_env\Lib\site-packages\stable_baselines3\common\buffers.py:242: UserWarning: This system does not have apparently enough memory to store the complete replay buffer 1.11GB > 0.91GB
  warnings.warn(


Logging to ./logs/DQN_2
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 106      |
|    ep_rew_mean      | 90       |
|    exploration_rate | 0.999    |
| time/               |          |
|    episodes         | 1        |
|    fps              | 30       |
|    time_elapsed     | 3        |
|    total_timesteps  | 106      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 56       |
|    ep_rew_mean      | 40       |
|    exploration_rate | 0.999    |
| time/               |          |
|    episodes         | 2        |
|    fps              | 30       |
|    time_elapsed     | 3        |
|    total_timesteps  | 112      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 39.3     |
|    ep_rew_mean      | 23.3     |
|    exploration_rate | 0.999    |
| time/               |        

In [41]:
from stable_baselines3 import DQN
from stable_baselines3.common.vec_env import DummyVecEnv, VecFrameStack
import time
import numpy as np

# ---------- ENV ----------
env = DummyVecEnv([make_env])
env = VecFrameStack(env, n_stack=4)

# ---------- LOAD BEST MODEL ----------
model = DQN.load("./best_model/best_model", env=env)

scores = []
best_score = 0
best_episode = -1

N_EPISODES = 10

print("🔍 Evaluating best model...\n")

for ep in range(N_EPISODES):
    obs = env.reset()
    done = False
    steps = 0

    while not done:
        action, _ = model.predict(obs, deterministic=True)
        obs, rewards, dones, infos = env.step(action)
        done = dones[0]
        steps += 1

        # Safety break (optional)
        if steps > 2000:
            break

    scores.append(steps)

    if steps > best_score:
        best_score = steps
        best_episode = ep

    print(f"Episode {ep:02d} | Steps survived: {steps}")
    time.sleep(0.5)

print("\n==============================")
print(f"BEST EPISODE : {best_episode}")
print(f"MAX STEPS    : {best_score}")
print(f"MEAN STEPS   : {np.mean(scores):.2f}")
print("==============================")
 

🔍 Evaluating best model...

Episode 00 | Steps survived: 6
Episode 01 | Steps survived: 6
Episode 02 | Steps survived: 140
Episode 03 | Steps survived: 6
Episode 04 | Steps survived: 140
Episode 05 | Steps survived: 6
Episode 06 | Steps survived: 140
Episode 07 | Steps survived: 6
Episode 08 | Steps survived: 141
Episode 09 | Steps survived: 6

BEST EPISODE : 8
MAX STEPS    : 141
MEAN STEPS   : 59.70


In [42]:
from stable_baselines3 import DQN
import time

env = DummyVecEnv([make_env])
env = VecFrameStack(env, n_stack=4)

model = DQN.load("./best_model/best_model", env=env)

obs = env.reset()
done = False
steps = 0

while not done:
    action, _ = model.predict(obs, deterministic=True)
    obs, rewards, dones, infos = env.step(action)
    done = dones[0]
    steps += 1
    time.sleep(0.01)

print("STEPS SURVIVED:", steps)


STEPS SURVIVED: 78
